In [7]:
!pip install tsai
!pip install numpy
!pip install pandas
!pip install matplotlib

Defaulting to user installation because normal site-packages is not writeable


Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


In [8]:
import pickle
from tsai.all import *

def backtest(
    arch, x, y, split_ratio= 0.8, file_path= None,
 n_epoch_retrain= 30, commision= 0.00, n_epoch_pretrain= 30, retraining_len= 50):
    
    pred_assets_cnt= len(y)//y.shape[0]
    entry= None
    entry_idx= None
    portf= 1.0
    prev_pred= None
    y_pred = []
    y_true = []
    returns= []
    train_size= int(x.shape[0]*split_ratio)
    test_size= x.shape[0] - train_size
    
    #pretrain model on train split   
    batch_tfms = TSStandardize(by_var=True)
    splt= get_splits(x[:train_size],train_only=True, show_plot =False)
    model = TSRegressor(
        x[:train_size], y[:train_size], 
        splits=splt, path='models',
        arch=arch, 
        batch_tfms=batch_tfms,
        metrics=rmse,verbose=False)
    model.fit_one_cycle(n_epoch_pretrain, 1e-2)
    pretrained= model.model

    for i in range(test_size-1):    
        X_train_current= x[:train_size+i]
        y_train_current=  y[:train_size+i]
        
        if retraining_len is not None:
            X_train_current= X_train_current[-retraining_len:]
            y_train_current=  y_train_current[-retraining_len:]
            
        splt= get_splits(X_train_current,train_only=True, show_plot =False)
        
        model = TSRegressor(
            X_train_current, y_train_current, 
            splits=splt, path='models',
            arch=arch, 
            batch_tfms=batch_tfms,
            metrics=rmse,verbose=False)
        
        model.model = pretrained
        with model.no_logging():
            model.fit_one_cycle(n_epoch_retrain, 1e-3)

        x_curr= np.expand_dims(x[train_size+i], 0)
        raw_preds, target, preds = model.get_X_preds(x)
       
        pred= preds.numpy()[-1][:]
        real= y[train_size+i]
        current= y[train_size+i-1]
        
        if len(current.shape) == 0:
            current = np.array([current])
            
        
        print(f"current price :{current}")
        print(f"current prediction:{pred}")
        
        if entry_idx is None:
            curr_trade_idx= np.argmax((pred - current) / current)
        else:
            curr_trade_idx= entry_idx

        if  current[curr_trade_idx] < pred[curr_trade_idx]:
            if entry is None:
                entry_idx= curr_trade_idx
                entry= current[curr_trade_idx]
                print(f"bought at {entry}, trade_asset_index: {entry_idx},  idx: {i}")
        else:
            if entry is not None:
                prof  = (current[entry_idx] / entry)*(1-commision)
                ret = (prof-1.0)*100
                portf= prof*portf
                print(f"exited at {current[entry_idx]}, profit:{ret}%,  portfolio: {portf*100}, \
                      trade_asset_index: {entry_idx} idx: {i}")
                returns.append(ret)
                entry= None
                entry_idx= None

        y_pred.append(pred)
        y_true.append(real)
        prev_pred= pred
        
    data= {"model": str(arch), 
           "split_ratio": split_ratio, 
           "returns": returns, 
           "result_portfolio_value": portf,
           "x":x,
           "y":y,
           "y_pred_test": np.array(y_pred),
           "y_true_test": np.array(y_true)}
    
    if file_path is not None:
        with open(file_path, 'wb') as f:
            pickle.dump(data, f)

    return portf, returns

In [9]:
import pandas as pd
import matplotlib.pyplot as plt
prices = pd.read_csv("./data_new/all_prices.csv", index_col= "date", parse_dates=True).resample("D").median(numeric_only=True)
trends= pd.read_csv("./data_new/all_trends.csv", index_col= "date", parse_dates=True).resample("D").mean(numeric_only=True)

TypeError: too many arguments passed in

In [ ]:
models_to_test= [InceptionTimePlus,XCM, GRUPlus,LSTMPlus, mWDNPlus, gMLP, OmniScaleCNN]
model_names= ['InceptionTimePlus','XCM', 'GRUPlus','LSTMPlus', 'mWDNPlus', 'gMLP', 'OmniScaleCNN']

In [ ]:
df= pd.concat([prices, trends], axis=1).dropna()
df= prices.dropna()

In [ ]:
import numpy as np
from tsai.all import *
from itertools import cycle, islice
from itertools import cycle, islice
df["day_of_week"]= df.index.dayofweek
df['month']= df.index.month
df['time_idx']= (range(len(df),0,-1))

# Split data into training and testing sets
X, y = SlidingWindow(100, horizon=1)(df.values)
price_indices= [df.columns.get_loc(c) for c in df.columns if 'price' in c]
y= y[:,price_indices].astype(np.float32) #only prices here (first 9 cols)
X= X.astype(np.float32)


In [ ]:
for m, model_name in zip(models_to_test, model_names):
    
    model = m(X.shape[-2], seq_len=X.shape[-1], c_out=y.shape[-1])
    print(f"{model_name} All data: \n")
    backtest(model, X, y, split_ratio= 0.7, commision= 0.0, n_epoch_retrain=20, file_path=f"./{model_name}")
    
    
  

In [ ]:
df